# Trafic Analyzer

## Ziel
Das Ziel ist es aus Verkehrszählungen in Zürich Daten wie Verkehrszuname über die Zeit zuanalysieren.

## Vorgehen

1. Daten einlesen
2. Daten validieren
3. Daten aufbereiten
4. Daten aggregieren
5. Daten auswerten

## Beschreibung der Datensätze
Die hier verfügbaren Datensätze beinhalten die täglich aktualisierten Messwerte zum motorisierten Individualverkehr (MIV) in der Stadt Zürich, welche von den zahlreichen Zählstellen der Dienstabteilung Verkehr (DAV) gemessen wurden.

Die Aktualisierung beinhaltet jeweils die Daten von vorgestern (z.B. am 17.1.2021 werden die Daten bis und mit dem vollendeten 15.1.2021 geliefert). Bis spätestens 08:00 Uhr sind die neuesten Daten verfügbar.

Zu einer Zählstelle gehören mehrere Messstellen, welche wiederum Messungen mit sogenannten Detektoren vornehmen. In den vorliegenden Datensätzen sind die Messwerte pro Zählstelle enthalten. Für jede Zählstelle gibt es einen detaillierten PDF-Situationsplan in der Datei "Zaehlstellen_Detail.zip", welcher u.a. die genaue Lage der Detektoren anzeigt.
  


## Umsetzung
### 1. Daten einlesen

In [22]:
import pandas as pd
import matplotlib.pyplot as plt

df = pd.read_csv("sid_dav_verkehrszaehlung_miv_od2031_2022.csv", sep=",", encoding="utf-8", low_memory=False)

### 2. Daten validieren 
Infos zu den Rohdaten

In [23]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1594138 entries, 0 to 1594137
Data columns (total 21 columns):
 #   Column              Non-Null Count    Dtype  
---  ------              --------------    -----  
 0   MSID                1594138 non-null  object 
 1   MSName              1594138 non-null  object 
 2   ZSID                1594138 non-null  object 
 3   ZSName              1594138 non-null  object 
 4   Achse               1594138 non-null  object 
 5   HNr                 1594138 non-null  object 
 6   Hoehe               1594138 non-null  object 
 7   EKoord              1594138 non-null  float64
 8   NKoord              1594138 non-null  float64
 9   Richtung            1594138 non-null  object 
 10  Knummer             1594138 non-null  int64  
 11  Kname               1594138 non-null  object 
 12  AnzDetektoren       1594138 non-null  int64  
 13  D1ID                1594138 non-null  int64  
 14  D2ID                1594138 non-null  object 
 15  D3ID           

Infos zu den Dimensionen

In [24]:
df.shape

(1594138, 21)

Datumstypen bereinigen

In [25]:
df["MessungDatZeit"] = pd.to_datetime(df["MessungDatZeit"])
df["LieferDat"] = pd.to_datetime(df["LieferDat"])

Auf mögliche Null-Daten Einträge überprüfen

In [26]:
df. isnull().sum()

MSID                       0
MSName                     0
ZSID                       0
ZSName                     0
Achse                      0
HNr                        0
Hoehe                      0
EKoord                     0
NKoord                     0
Richtung                   0
Knummer                    0
Kname                      0
AnzDetektoren              0
D1ID                       0
D2ID                       0
D3ID                       0
D4ID                       0
MessungDatZeit             0
LieferDat                  0
AnzFahrzeuge          115327
AnzFahrzeugeStatus         0
dtype: int64

Fehlende Daten identifizeren

In [27]:
# Find rows with missing values
missing_data = df[df.isnull().any(axis=1)]

# Group by ZSName, MessungDatZeit, and Richtung to count the number of missing entries
missing_data_grouped = missing_data.groupby(['ZSName', missing_data['MessungDatZeit'].dt.date, 'Richtung']).size().reset_index(name='Anzahl_Missing')

# Pivot the table to have dates as columns and ZSName as rows
missing_data_pivot = missing_data_grouped.pivot_table(index=['ZSName', 'Richtung'], columns='MessungDatZeit', values='Anzahl_Missing', fill_value=0)

# Display the pivot table
#display(missing_data_pivot)


In [28]:
import seaborn as sns

# Erstellen einer Heatmap der fehlenden Daten
plt.figure(figsize=(40, 40), dpi=300)
sns.heatmap(missing_data_pivot, cmap="YlGnBu", cbar_kws={'label': 'Anzahl fehlender Daten'})

# Hinzufügen horizontaler Linien
for i in range(len(missing_data_pivot.index)):
    plt.axhline(i, color='gray', linestyle='--', linewidth=0.5)

plt.title('Fehlende Daten pro ZSName und Datum')
plt.xlabel('Datum')
plt.ylabel('ZSName')
plt.xticks(rotation=45)
plt.tight_layout()
plt.show()

Daten bereinigen

In [34]:
# Calculate the total number of hours in a year (365 days * 24 hours)
total_hours_in_year = 365 * 24

# Group by ZSName and Richtung, then sum the Anzahl_Missing to get the total missing hours per ZSName and Richtung
missing_hours_per_zsname_richtung = merged_data.groupby(['ZSName', 'Richtung'])['Anzahl_Missing'].sum().reset_index()

# Calculate the ratio of missing hours in relation to the total hours in a year
missing_hours_per_zsname_richtung['Missing_Ratio'] = missing_hours_per_zsname_richtung['Anzahl_Missing'] / total_hours_in_year

# Display the result
print(missing_hours_per_zsname_richtung)

                                       ZSName           Richtung  \
0             A3W (A4 Uetlibergtunnel Brunau)    Uetlibergtunnel   
1             A3W (A4 Uetlibergtunnel Brunau)           einwärts   
2                           A3W (Chur Brunau)               Chur   
3                           A3W (Chur Brunau)           einwärts   
4               Albisriederstrasse (Hubertus)   Albisriederplatz   
..                                        ...                ...   
132  Winterthurerstrasse (Luchswiesenstrasse)           auswärts   
133  Winterthurerstrasse (Luchswiesenstrasse)           einwärts   
134                           Wipkingerbrücke  Escher Wyss Platz   
135                           Wipkingerbrücke     Wipkingerplatz   
136              Zollikerstrasse (Höschgasse)           einwärts   

     Anzahl_Missing  Missing_Ratio  
0               435       0.049658  
1                 4       0.000457  
2                 4       0.000457  
3                 4       0.000457 